In [1]:
%load_ext autoreload
%autoreload 2

import os
import sys

module_path = os.path.abspath(os.path.join('../..'))
if module_path not in sys.path:
    sys.path.append(module_path)

import torch
import pandas as pd
import numpy as np
import pickle
import geopandas as gpd

from pipelines.utils import ROOT_DIR, load_config, load_road_network


os.environ["CUDA_DEVICE_ORDER"] = "PCI_BUS_ID"
os.environ["CUDA_VISIBLE_DEVICES"] = "0"
device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')

In [2]:
data_config = load_config(name='porto', ctype="dataset")

# Load CellSpace
dataset_cell_file = f"{data_config['city']}_cell{int(data_config['cell_size'])}_cellspace.pkl"
file_path = os.path.join(ROOT_DIR, "models/road_embs/", dataset_cell_file)
with open(file_path, 'rb') as fh:
    cs = pickle.load(fh)
cs_gdf = cs.get_celldf()

# Load Feats Matrix
feats_mx_file = f"{data_config['city']}_cell{int(data_config['cell_size'])}_feats_mx.pkl"
file_path = os.path.join(ROOT_DIR, "models/road_embs/", feats_mx_file)
with open(file_path, 'rb') as fh:
    feats_mx = pickle.load(fh)



In [3]:
# Load Trajectories
file_path = os.path.join(
                ROOT_DIR,
                "datasets/trajectory",
                data_config['city'],
                "trajectories_mapped_road_stamps.parquet")
# Train dataset
traj_data = pd.read_parquet(file_path)

# Load Road Network
edge_df, node_df, G, LG = load_road_network(data_config["city"])

In [4]:
# For testing
#traj_data = traj_data.iloc[:1000000]

In [37]:
# Time for all: 1.15s
# time for 500k 35s
# time for 100k 20s
def get_list_of_linestrings(traj_data, edge_df):
    # Create a new dataframe that contains the index of traj_data and the cpath column
    traj_data_idx = traj_data.reset_index()[['index', 'cpath']]
    edge_geom_df = edge_df.reset_index()['geometry']

    # Explode the cpath column into multiple rows
    traj_data_idx = traj_data_idx.explode('cpath')

    # Merge traj_data_idx with edge_df on the cpath column
    merged_df = pd.merge(traj_data_idx, edge_geom_df, left_on='cpath', right_index=True)

    # Group merged_df by the index of traj_data and aggregate the geometry column into a list
    ls_list = merged_df.groupby('index')['geometry'].agg(list)
    return ls_list

ls_list = get_list_of_linestrings(traj_data, edge_df)

In [38]:
# time for all 15 min
# timee for 500k 7min
def get_list_of_cell_seq(ls_list, cs_gdf):
    # Create a new GeoDataFrame that contains the exploded linestrings
    linestrings_gdf = gpd.GeoDataFrame(geometry=pd.Series(ls_list).explode().reset_index(drop=True)).set_crs(cs_gdf.crs)
    linestrings_gdf.sindex

    cs_gdf_geom = cs_gdf[['cell_id','geometry']]
    cs_gdf_geom.sindex
    # Perform a spatial join between linestrings_gdf and cs_gdf
    intersecting_cells = gpd.sjoin(linestrings_gdf, cs_gdf_geom, op='intersects')

    # This was 10% slower
    # cell_sequences1 = intersecting_cells.groupby(intersecting_cells.index)['cell_id'].agg(list).tolist()

    # Group intersecting_cells by the index of linestrings_gdf and aggregate the cell_id column into a list
    cell_sequences_dict = {k: list(v) for k, v in intersecting_cells.groupby(intersecting_cells.index)['cell_id']}
    # Convert the dictionary values into a list
    cell_sequences = list(cell_sequences_dict.values())
    return cell_sequences

cell_sequences = get_list_of_cell_seq(ls_list, cs_gdf)

In [39]:
# time for 500k 35s

# create a transition matrix to count the number of transitions between cells
num_cells = len(cs_gdf)
transition_matrix = np.zeros((num_cells, num_cells))

# loop through the cell_sequences and update the transition counts in the transition matrix
for cell_sequence in cell_sequences:
    for i in range(len(cell_sequence) - 1):
        from_cell = cell_sequence[i]
        to_cell = cell_sequence[i+1]
        transition_matrix[from_cell, to_cell] += 1

In [9]:
transition_matrix.shape

(36252, 36252)

In [28]:
def count_nonzero_zero(arr: np.ndarray):
    nonzero = np.count_nonzero(arr)
    zero = arr.size - nonzero
    print(f"Number of non-zero elements: {nonzero}")
    print(f"Number of zero elements: {zero}")
    print(f"Ratio of non-zero elements: {nonzero / arr.size}")

count_nonzero_zero(transition_matrix)


Number of non-zero elements: 8276
Number of zero elements: 1314199228
Ratio of non-zero elements: 6.297331262232695e-06


In [42]:
np.savez("cell_trans-mx.npz", transition_matrix)

In [5]:
transition_matrix = np.load("cell_trans-mx.npz")['arr_0']

In [6]:
transition_matrix

array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]])

In [ ]:
# Next:
# I want the transition matrix to be symetric along diagonal (we regard in and outflow as same)
np.diag(transition_matrix.diagonal())

In [13]:
symmetric_matrix = transition_matrix + transition_matrix.T

In [7]:
cells_idx = np.logical_or(np.any(transition_matrix, axis=0), np.any(transition_matrix, axis=1))

In [8]:
gdf = cs_gdf[cells_idx]

In [9]:
import folium


# Create a Folium map centered at the centroid of your polygons
m = folium.Map(location=gdf.geometry.centroid.iloc[0].coords[:][0][::-1], zoom_start=10)


# Add each polygon to the map as a separate layer
for _, row in gdf.iterrows():
    folium.GeoJson(row['geometry']).add_to(m)

# Display the map
m


/tmp/ipykernel_3118433/3706394842.py:5: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  m = folium.Map(location=gdf.geometry.centroid.iloc[0].coords[:][0][::-1], zoom_start=10)
